In [13]:
import pandas as pd
from IPython.display import HTML
from tqdm import tqdm
#from visualize import *
import sys
sys.path.insert(0, 'models')
import numpy as np

pd.set_option('display.max_columns', 200)
pd.set_option('display.max_rows', 100)
np.warnings.filterwarnings('error', category=np.VisibleDeprecationWarning) 

In [14]:
from play_eppa_gpu import *

In [3]:
path_shared = '../data/{}'
games_df = pd.read_csv(path_shared.format('games.csv'))
plays_df = pd.read_csv(path_shared.format('plays.csv'))
players_df = pd.read_csv(path_shared.format('players.csv'))
track_df1 = pd.read_csv(path_shared.format('week1_norm.csv'))
track_df2 = pd.read_csv(path_shared.format('week2_norm.csv'))
track_df4 = pd.read_csv(path_shared.format('week4_norm.csv'))
track_df7 = pd.read_csv(path_shared.format('week7_norm.csv'))
track_df6 = pd.read_csv(path_shared.format('week6_norm.csv'))
track_df10 = pd.read_csv(path_shared.format('week10_norm.csv'))
track_df16 = pd.read_csv(path_shared.format('week16_norm.csv'))
track_df15 = pd.read_csv(path_shared.format('week15_norm.csv'))
track_df14 = pd.read_csv(path_shared.format('week14_norm.csv'))

In [4]:
track_df5 = pd.read_csv(path_shared.format('week5_norm.csv'))
track_df6 = pd.read_csv(path_shared.format('week6_norm.csv'))

In [5]:
track_df13 = pd.read_csv(path_shared.format('week13_norm.csv'))

In [6]:
plays = list(set(map(lambda x: (x[0].item(), x[1].item()), track_df.groupby(['gameId', 'playId'], as_index=False).first()[['gameId', 'playId']].to_numpy())))
len(plays)

NameError: name 'track_df' is not defined

In [15]:
# deep lockett vs chiefs (16)
# game_id = 2018122314
# play_id = 4239

# deep dissly vs bears (2)
# game_id = 2018091700
# play_id = 3936

# deep middle gronk 2 v 1 (1) 
# game_id = 2018090905
# play_id = 2062

# TRUEVIEW
# gronk td (1)
# game_id = 2018090905
# play_id = 228

# olsen over underneath cov (1)
# game_id = 2018090910
# play_id = 806

# kirk sack (13)
# game_id = 2018120212
# play_id = 3103

# kirk to thielen cool route (13)
# game_id = 2018120212
# play_id = 1834

# brady to flash seam in zone (13)
game_id = 2018120212
play_id = 2971

## END TRUEVIEW ###

### ROUTE COMBOS ####
#game_id = 2018091604
#play_id = 2613

# game_id = 2018091700
# play_id = 1959

# detroit red zone vs jets (1)
# game_id = 2018091000
# play_id = 3016

# ten adoree jackson high eppa (1)
# game_id = 2018090903
# play_id = 1515																													

# mullens to kittle, def by wagner (13)
# game_id = 2018120213
# play_id = 398

# mullens to bobby, 98yd pick6 (13)
# game_id = 2018120213
# play_id = 3952

# mahomes to tyreek, KJ defense (16)
# game_id = 2018122314
# play_id = 73

#random debug play
# game_id = 2018090912
# play_id = 3564

# game_id, play_id = random.choice(plays)

play_df = track_df[(track_df.playId == play_id) & (track_df.gameId == game_id)].sort_values(by = 'frameId')

ball_snap_frame = play_df.loc[(play_df.nflId == 0) & (play_df.event == 'ball_snap')].frameId.iloc[0]
# pass_forward_frame = play_df.loc[(play_df.nflId == 0) & (play_df.event == 'pass_forward')].frameId.iloc[0]

# play_df['frames_since_snap'] = play_df.frameId - ball_snap_frame
# play_df = play_df.join(los, on=['gameId', 'playId'])
play_df.reset_index(drop=True, inplace=True)

play_df.head()

NameError: name 'track_df' is not defined

In [7]:
game_id = 2018101404
play_id = 977
play_df, field_dfs, passes_df, player_stats_df = play_eppa_gpu(track_df6, game_id, play_id, viz_df=True, save_np=False, stats_df=True, viz_true_proj=True, save_all_dfs= False)

100%|██████████| 12/12 [00:09<00:00,  1.32it/s]


In [ ]:
out_dir_path = '../output/{}'
opt_play_df = pd.read_csv(out_dir_path.format(f'def_opt_output/horizon_1_5/def_opt_{game_id}_{play_id}/opt_play_df.csv'), index_col=0)
opt_play_df.loc[opt_play_df.team_pos=='DEF', ['x', 'y', 'v_x', 'v_y', 'a_x', 'a_y']] = \
    opt_play_df.loc[opt_play_df.team_pos=='DEF', ['x_opt', 'y_opt', 'v_x_opt', 'v_y_opt', 'a_x_opt', 'a_y_opt']].rename(columns=(lambda x: x.replace('_opt', '')))
opt_play_df.loc[(opt_play_df.team_pos=='DEF')].tail()

In [ ]:
play_df2, field_dfs2, passes_df2, player_stats_df2 = play_eppa_gpu(opt_play_df, game_id, play_id, viz_df=True, save_np=False, stats_df=True, viz_true_proj=False, save_all_dfs= False)

In [ ]:
maxFid = opt_play_df.frameId.max()
opt_play_df.loc[(opt_play_df.team_pos=='OFF')&(opt_play_df.frameId>=14)&(opt_play_df.frameId<=maxFid-8), ['proj_x', 'proj_y', 'proj_v_x', 'proj_v_y', 'proj_a_x', 'proj_a_y']] = \
    opt_play_df.loc[(opt_play_df.team_pos=='OFF')&(opt_play_df.frameId>=22), ['x_opt', 'y_opt', 'v_x_opt', 'v_y_opt', 'a_x_opt', 'a_y_opt']].to_numpy()
opt_play_df.loc[(opt_play_df.team_pos=='DEF')&(opt_play_df.frameId>=14)&(opt_play_df.frameId<=maxFid-8), ['proj_x', 'proj_y', 'proj_v_x', 'proj_v_y', 'proj_a_x', 'proj_a_y']] = \
    opt_play_df.loc[(opt_play_df.team_pos=='DEF')&(opt_play_df.frameId>=14)&(opt_play_df.frameId<=maxFid-8), ['x_opt', 'y_opt', 'v_x_opt', 'v_y_opt', 'a_x_opt', 'a_y_opt']].to_numpy()

In [12]:
animated_play = AnimatePlay(play_df, 20, field_dfs.rename(columns={'eppa1s': 'v_mass'}))
HTML(animated_play.ani.to_jshtml())

58


/home/ambi/.virtualenvs/big_data_bowl/lib/python3.8/site-packages/numpy/core/_asarray.py:136: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order, subok=True)
/home/ambi/.virtualenvs/big_data_bowl/lib/python3.8/site-packages/numpy/core/_asarray.py:136: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order, subok=True)
/home/ambi/.virtualenvs/big_data_bowl/lib/python3.8/site-packages/numpy/core/_asarray.py:136: VisibleDeprecationWarning: Creating an ndarray from ragged neste

/home/ambi/.virtualenvs/big_data_bowl/lib/python3.8/site-packages/numpy/core/_asarray.py:136: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order, subok=True)
/home/ambi/.virtualenvs/big_data_bowl/lib/python3.8/site-packages/numpy/core/_asarray.py:136: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order, subok=True)
/home/ambi/.virtualenvs/big_data_bowl/lib/python3.8/site-packages/numpy/core/_asarray.py:136: VisibleDeprecationWarning: Creating an ndarray from ragged neste

/home/ambi/.virtualenvs/big_data_bowl/lib/python3.8/site-packages/numpy/core/_asarray.py:136: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order, subok=True)
/home/ambi/.virtualenvs/big_data_bowl/lib/python3.8/site-packages/numpy/core/_asarray.py:136: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order, subok=True)
/home/ambi/.virtualenvs/big_data_bowl/lib/python3.8/site-packages/numpy/core/_asarray.py:136: VisibleDeprecationWarning: Creating an ndarray from ragged neste

In [10]:
animated_play = AnimatePlay(opt_play_df, 20, field_dfs2.rename(columns={'eppa1s': 'v_mass'}), viz_proj=True)
HTML(animated_play.ani.to_html5_video())

NameError: name 'opt_play_df' is not defined

In [ ]:
with open('test.html', 'w+') as out:
    out.write(animated_play.ani.to_jshtml())

In [ ]:
print(animated_play.ani._frames)
animated_play.ani.save('test.gif', writer='imagemagick', fps=30)

In [ ]:
animated_play = AnimatePlay(play_df, 20, field_dfs.rename(columns={'ppc_off': 'p_mass'}))
animated_play.ani.save()

In [ ]:
animated_play = AnimatePlay(play_df, 20, field_dfs.rename(columns={'trans': 'p_mass'}))
HTML(animated_play.ani.to_jshtml())

In [ ]:
animated_play = AnimatePlay(play_df2, 20, field_dfs2.rename(columns={'trans': 'v_mass'}))
HTML(animated_play.ani.to_jshtml())

In [ ]:
type(animated_play.ani)
animated_play.ani.save('./results/test.gif', writer='imagemagick', fps=10)

In [ ]:
pd.merge(passes_df[['gameId', 'playId', 'frameId','eppa1_tot']], passes_df2[['gameId', 'playId', 'frameId','eppa1_tot']], on=['gameId', 'playId', 'frameId'])